This script performs LOO test on HLCA dataset using RAPToR pipeline

In [1]:
import scanpy as sc
import pandas as pd
import numpy as np
import seaborn as sns
import sklearn
from tqdm import tqdm
from functools import reduce

Read HLCA data

In [2]:
hlca_smoker = sc.read_h5ad("data/step1_HLCA_smoker_processed.h5ad")
hlca_nonsmoker = sc.read_h5ad("data/step1_HLCA_nonsmoker_processed.h5ad")

Keep only these columns

In [3]:
hlca_smoker.obs = hlca_smoker.obs.loc[:,['donor_id',
                                       'age',
                                       'ann_level_1',
                                       'ann_level_2',
                                       'ann_level_3',
                                       'ann_level_4',
                                       'ann_level_5']
                                     ]
hlca_nonsmoker.obs = hlca_nonsmoker.obs.loc[:,['donor_id',
                                       'age',
                                       'ann_level_1',
                                       'ann_level_2',
                                       'ann_level_3',
                                       'ann_level_4',
                                       'ann_level_5']
                                     ]

## Modeling

In [4]:
from sklearn.metrics import r2_score, mean_absolute_error
from sklearn.metrics import mean_absolute_error

from functools import partial,reduce

Data filtering by Number of Cells

In [5]:
'''
Filter anndata by cell type, marker genes, and subjects. Subjects are selected by min_cells
Return filtered expression matrix and ages.
'''
def filter_anndata_single_ct(anndata, ct_column, ct, donor_column, age_column, marker_genes = None, min_cells = 20):
        
    # Keep rows annotated with current cell type, and columns annotated with marker genes,  
    ct_anndata = anndata[anndata.obs[ct_column] == ct, :]
    ct_anndata = ct_anndata[:, ct_anndata.var_names.isin(marker_genes)]
    
    # Select subjects having number of cells greater than min_cells 
    subjects = ct_anndata.obs[donor_column]
    subjects_count = subjects.groupby(subjects.values).count()
    selected_subjects = subjects_count.loc[subjects_count >= min_cells].index 
    
    # Further subset anndata using the selected subjects
    ct_anndata = ct_anndata[ct_anndata.obs[donor_column].isin(selected_subjects),]
    
    # Generate filtered expression matrix and ages
    expr = ct_anndata.to_df()
    expr.index = ct_anndata.obs[donor_column].values
    ages = ct_anndata.obs[age_column]
    ages.index = expr.index
        
    return expr, ages

In [6]:
def compute_features(expr, ages, mean_degree, var_degree, n_components, use_pca, pca_model):

    if use_pca and pca_model is None:
        pca_model = PCA(n_components=n_components, whiten=True)
        expr = pd.DataFrame(pca_model.fit_transform(expr), index = expr.index)
        expr.columns = [f"PC{i+1}" for i in range(expr.shape[1])]
    elif use_pca and pca_model is not None:
        expr = pd.DataFrame(pca_model.transform(expr), index = expr.index)
        expr.columns = [f"PC{i+1}" for i in range(expr.shape[1])]
        
    # Get each subject/individual's mean expression and polynomials of mean expressions.
    subjects = expr.index.to_list()
    expr_mean = expr.groupby(subjects).mean()
    expr_mean_poly = np.hstack([expr_mean**i for i in range(1, mean_degree+1)])
    feature_names = np.hstack([[f"{col}_mean^{deg}" for col in expr.columns] for deg in range(1,mean_degree+1)]) # Name the polynomial features
    expr_mean_poly = pd.DataFrame(
                        expr_mean_poly,
                        index = expr_mean.index,
                        columns = feature_names 
                    )
    
    if var_degree > 0:

        # Get each subject/indivisual's variances.
        expr_var = expr.groupby(subjects).var()
        expr_var.fillna(value=0,inplace=True) # This should not happen 
        expr_var_poly = np.hstack([expr_var**i for i in range(1, var_degree+1)])
        feature_names = np.hstack([[f"{col}_var^{deg}" for col in expr.columns] for deg in range(1,var_degree+1)]) # Name the polynomial features
        expr_var_poly = pd.DataFrame(
                        expr_var_poly,
                        index = expr_var.index,
                        columns = feature_names 
                    )

        # Concatenate mean and var polynomial features
        X = pd.concat([expr_mean_poly,expr_var_poly],axis = 1)
    else:
        X = expr_mean_poly
    
    # Get Y
    Y = ages.groupby(subjects).mean()
    
    return X,Y,pca_model

Generate data for feature extraction and training/testing

In [7]:
import warnings
warnings.filterwarnings("ignore")

iterator = []
n_rep = 5
donor_types = ["nonsmoker","smoker"]
adatas = [hlca_nonsmoker,hlca_smoker]

for annLevel in ['ann_level_2','ann_level_3','ann_level_4','ann_level_5']:
    c1 = hlca_nonsmoker.obs[annLevel]
    c2 = hlca_smoker.obs[annLevel]
    cell_types = np.union1d(c1,c2)
    selected_cell_types = []
    
    for adata,group in zip(adatas,donor_types):
        for ct in cell_types:
            
            # Get donor number
            adata_ct = adata[adata.obs[annLevel] == ct,]
            expr,ages = filter_anndata_single_ct(adata_ct,
                                     ct_column = annLevel,
                                     ct = ct,
                                     donor_column = "donor_id",
                                     age_column = "age",
                                     marker_genes = adata.var_names,
                                     min_cells = 20
                                    )
            all_donor = expr.index.unique()
            all_donor_num = all_donor.shape[0]
            
            del(adata_ct)
            if all_donor_num >= 10 and ct != "None":
                selected_cell_types.append(ct)
                for use_pca in [False]:
                    for rep in range(1,n_rep+1):
                        iterator.append([expr,ages,group,ct,annLevel,f"all_{group}",use_pca,rep,all_donor_num])

Train and test models

In [8]:
def train_test_loo(expr, ages, use_pca, subject_type, ct):
    
    subjects = expr.index.unique()
    Y_trues = []
    Y_preds = []
    Y_trues_untrans = []
    Y_preds_untrans = []
    
    # Leave-one-out test
    for subj in subjects:
        
        test_subjects = [subj]
        train_subjects = subjects[~subjects.isin(test_subjects)]
        
        X_train = expr.loc[expr.index.isin(train_subjects),]
        Y_train = ages.loc[ages.index.isin(train_subjects),]
        X_test = expr.loc[expr.index.isin(test_subjects),]
        Y_test = ages.loc[ages.index.isin(test_subjects),]
        
        # Note that PCA trained on training data was used on test data.
        X_train, Y_train, pca_model = compute_features(X_train, Y_train, mean_degree=1, var_degree=0, n_components=10, use_pca = use_pca, pca_model=None)
        X_test, Y_test, _ = compute_features(X_test, Y_test, mean_degree=1, var_degree=0, n_components=10, use_pca=use_pca, pca_model = pca_model)
        
        # Reformat inputs for RAPToR model
        Y_train = pd.DataFrame(Y_train, columns = ["age"])
        X_train = X_train.transpose()
        X_test = X_test.transpose()

        # Activate R environment and import R packages inside this process
        from rpy2.robjects import pandas2ri
        from rpy2.robjects.packages import importr
        from rpy2.rinterface_lib.embedded import RRuntimeError

        pandas2ri.activate()

        base = importr('base')
        utils = importr('utils')

        # Note this should be the exact location where conda R library is located
        # Please replace it with the path of the environment on your machine
        raptor = importr('RAPToR', lib_loc="/jet/home/qsong/.conda/envs/lung_aging/lib/R/library")
        
        # Build RAPToR reference model with default parameters. If RAPToR model runs into error, use np.nan as prediction result
        # Note that nc should be smaller than or equal to the number of samples.
        try:
            if X_train.shape[1] >= 10:
                model = raptor.ge_im(X = X_train,
                     p = Y_train,
                     formula = "X ~ s(age, bs = 'ts')",
                     nc = 10
                    )
            else:
                model = raptor.ge_im(X = X_train,
                     p = Y_train,
                     formula = "X ~ s(age, bs = 'ts')",
                     nc = X_train.shape[1]
                    )
        except RRuntimeError:
            Y_trues.append(np.nan)
            Y_preds.append(np.nan)
            print(f"{ct} in {subject_type} failed with RAPToR")
            break
        else:    
            ref = raptor.make_ref(m = model,
                   n_inter = 100, # interpolation resolution
                   t_unit = "Year", # time unit
                  )

            # Get predicted ages for testing set
            Y_trues.append(Y_test.values[0])
            Y_preds.append(raptor.ae(X_test, ref)[0][0,0])
        
    # Compute R2 and MAE as evaluation metrics
    Y_trues = np.hstack(Y_trues)
    Y_preds = np.hstack(Y_preds)
    
    if np.any(np.isnan(Y_preds)):
        r2 = None
        MAE = None
    else:
        r2 = r2_score(Y_trues, Y_preds)
        MAE = mean_absolute_error(Y_trues, Y_preds)
    
    return r2,MAE,Y_trues,Y_preds

### Main analysis pipeline

In [35]:
from joblib import delayed, Parallel
import warnings

def run_all(expr, ages, group, ct, ct_column, gene_type, use_pca, all_donor_num, rep):
    warnings.filterwarnings("ignore")
    
    # Run leave-one-out test for current cell type
    r2,MAE,Y_trues,Y_preds = train_test_loo(expr, ages, use_pca, subject_type = group, ct = ct)
    
    if np.any(np.isnan(Y_preds)):
        Y_trues = None
        Y_preds = None
    else:
        Y_trues = ",".join([str(age) for age in Y_trues])
        Y_preds = ",".join([str(age) for age in Y_preds])
    
    return ct_column,group,ct,gene_type,use_pca,r2,rep,all_donor_num,Y_trues,Y_preds


res = Parallel(n_jobs = 20)(delayed(run_all)(
                                          expr,
                                          ages,
                                          group,
                                          ct,
                                          ct_column,
                                          gene_type,
                                          use_pca,
                                          all_donor_num,
                                          rep = rep) for expr,ages,group,ct,ct_column,gene_type,use_pca,rep,all_donor_num in tqdm(iterator[20:]))





  0%|          | 0/430 [00:00<?, ?it/s]



  5%|▍         | 20/430 [00:02<00:53,  7.61it/s]R[write to console]: Error in smooth.construct.tp.smooth.spec(object, data, knots) : 
  A term has fewer unique covariate combinations than specified maximum degrees of freedom

R[write to console]: In addition: 
R[write to console]: Warning messages:

R[write to console]: 1: 
R[write to console]: In (function (package, help, pos = 2, lib.loc = NULL, character.only = FALSE,  :
R[write to console]: 
 
R[write to console]:  library ‘/usr/share/R/library’ contains no packages

R[write to console]: 2: 
R[write to console]: In (function (package, help, pos = 2, lib.loc = NULL, character.only = FALSE,  :
R[write to console]: 
 
R[write to console]:  library ‘/usr/share/R/library’ contains no packages

R[write to console]: Error in smooth.construct.tp.smooth.spec(object, data, knots) : 
  A term has fewer unique covariate combinations than specified maximum degrees of freedom

R[write to console]: I

R[write to console]: Bootstrapping...

R[write to console]: 	Building gene subsets...

R[write to console]: 	Computing correlations...

R[write to console]: 	Performing age estimation...

R[write to console]: 	Performing age estimation...

R[write to console]: Computing summary statistics...

R[write to console]: Computing summary statistics...

R[write to console]: Bootstrap set size is 9038

R[write to console]: Performing age estimation...

R[write to console]: Bootstrapping...

R[write to console]: 	Building gene subsets...

R[write to console]: 	Computing correlations...

R[write to console]: 	Performing age estimation...

R[write to console]: Computing summary statistics...

R[write to console]: Bootstrap set size is 9038

R[write to console]: Bootstrap set size is 9038

R[write to console]: Bootstrap set size is 9038

R[write to console]: Bootstrap set size is 9038

R[write to console]: Performing age estimation...

R[write to console]: Performing age estimation...

R[write to c

R[write to console]: 	Performing age estimation...

R[write to console]: Performing age estimation...

R[write to console]: Computing summary statistics...

R[write to console]: Bootstrapping...

R[write to console]: 	Building gene subsets...

R[write to console]: 	Computing correlations...

R[write to console]: 	Performing age estimation...

R[write to console]: Computing summary statistics...

R[write to console]: Bootstrap set size is 9038

R[write to console]: 	Performing age estimation...

R[write to console]: Performing age estimation...

R[write to console]: Computing summary statistics...

R[write to console]: Bootstrapping...

R[write to console]: 	Building gene subsets...

R[write to console]: 	Computing correlations...

R[write to console]: 	Performing age estimation...

R[write to console]: Bootstrap set size is 9038

R[write to console]: Bootstrap set size is 9038

R[write to console]: Computing summary statistics...

R[write to console]: Bootstrap set size is 9038

R[writ

R[write to console]: Bootstrap set size is 9038

R[write to console]: Performing age estimation...

R[write to console]: Bootstrap set size is 9038

R[write to console]: Performing age estimation...

R[write to console]: Bootstrapping...

R[write to console]: 	Building gene subsets...

R[write to console]: 	Computing correlations...

R[write to console]: Bootstrapping...

R[write to console]: 	Building gene subsets...

R[write to console]: 	Computing correlations...

R[write to console]: Bootstrap set size is 9038

R[write to console]: Bootstrap set size is 9038

R[write to console]: 	Performing age estimation...

R[write to console]: 	Performing age estimation...

R[write to console]: Bootstrap set size is 9038

R[write to console]: Computing summary statistics...

R[write to console]: Performing age estimation...

R[write to console]: Computing summary statistics...

R[write to console]: Performing age estimation...

R[write to console]: 	Performing age estimation...

R[write to cons

R[write to console]: Bootstrapping...

R[write to console]: 	Building gene subsets...

R[write to console]: 	Computing correlations...

R[write to console]: Performing age estimation...

R[write to console]: Bootstrapping...

R[write to console]: 	Building gene subsets...

R[write to console]: 	Computing correlations...

R[write to console]: Performing age estimation...

R[write to console]: Bootstrapping...

R[write to console]: 	Building gene subsets...

R[write to console]: 	Computing correlations...

R[write to console]: 	Performing age estimation...

R[write to console]: 	Performing age estimation...

R[write to console]: Computing summary statistics...

R[write to console]: Computing summary statistics...

R[write to console]: 	Performing age estimation...

R[write to console]: Computing summary statistics...

R[write to console]: 	Performing age estimation...

R[write to console]: Computing summary statistics...

R[write to console]: Bootstrap set size is 9038

R[write to consol

...

R[write to console]: There were 50 or more warnings (use warnings() to see the first 50)
R[write to console]: 



EC general capillary in smoker failed with RAPToR


R[write to console]: There were 50 or more warnings (use warnings() to see the first 50)
R[write to console]: 

R[write to console]: There were 50 or more warnings (use warnings() to see the first 50)
R[write to console]: 

R[write to console]: There were 50 or more warnings (use warnings() to see the first 50)
R[write to console]: 



Lymphatic EC in smoker failed with RAPToR
AT1 in smoker failed with RAPToR
AT1 in smoker failed with RAPToR


R[write to console]: There were 50 or more warnings (use warnings() to see the first 50)
R[write to console]: 



Save results

In [36]:
to_save = pd.DataFrame(res, columns = ["ann_level","group","cell_type","gene_type","use_pca","R2","rep","all_donor_num","true_age","pred_age"])

remove "[" and "]"

In [38]:
import re

In [39]:
dfs = []
for grp,df in to_save.groupby(["ann_level","group","cell_type","gene_type","use_pca"]):
    df["R2_mean"] = df["R2"].mean()
    df["R2_std"] = df["R2"].std()
    del(df["R2"])
    del(df["rep"])
    dfs.append(df.drop_duplicates())
dfs = pd.concat(dfs)

to_save = to_save.sort_values(by = "R2", ascending = False)

if not os.path.isdir("results/eval"):
    os.mkdir("results/eval")    
to_save.to_csv(f"results/eval/performances_HLCA_loo_RAPToR.csv",index = None)